In [1]:
import gensim
from gensim.models.doc2vec import Doc2Vec
from gensim.models.phrases import Phrases, Phraser
from gensim import corpora
from collections import namedtuple
import os
import pandas as pd
import csv
import sys

In [2]:
class CorpusIterator:
    def __init__(self, folder_path, bigram=None, trigram=None):
        self.folder_path = folder_path
        self.bigram = bigram
        self.trigram = trigram

    def __iter__(self):
        Speeches = namedtuple('speeches', 'words tags')
        for root, dirs, files in os.walk(self.folder_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    print(f"Processing {file_path}")
                    with open(file_path, 'r', newline='', encoding='utf-8') as f:
                        reader = csv.DictReader(f, delimiter=',')
                        for row in reader:
                            text = row['speechtext_preprocessed']
                            congress = str(row['speechdate'].split('-')[0])
                            party = row['speakerparty']
                            partytag = party + '_' + congress
                            congresstag = 'CONGRESS_' + congress
                            tokens = text.split()
                            if self.bigram and self.trigram:
                                words = self.trigram[self.bigram[tokens]]
                            elif self.bigram and not self.trigram:
                                words = self.bigram[tokens]
                            else:
                                words = tokens
                            tags = [partytag, congresstag]
                            yield Speeches(words, tags)

class PhraseIterator:
    def __init__(self, folder_path):
        self.folder_path = folder_path

    def __iter__(self):
        # Increase the field size limit- I was running into issues with csv exceeding the default limit in csv packaga
        csv.field_size_limit(sys.maxsize)
        
        # instead of just taking in one file with all the text, this will iterate through every folder in my folder path
        for root, dirs, files in os.walk(self.folder_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    print(f"Processing {file_path}")
                    with open(file_path, 'r', newline='', encoding='utf-8') as f:
                        reader = csv.DictReader(f, delimiter=',')
                        for row in reader:
                            text = row['speechtext_preprocessed']
                            yield text.split()


In [3]:
# trying this shit one more time
class corpusIterator(object):

    def __init__(self, inpath, house, bigram=None, trigram=None):
        if bigram:
            self.bigram = bigram
        else:
            self.bigram = None
        if trigram:
            self.trigram = trigram
        else:
            self.trigram = None
        self.house = house
        self.inpath = inpath

    def __iter__(self):
        self.speeches = namedtuple('speeches', 'words tags')
        with open(self.inpath, 'r', newline='', encoding='utf-8') as f:
            reader = csv.DictReader(f)
            for row in reader:
                text = row['speechtext_preprocessed']
                congress = str(row['speechdate'].split('-')[0])
                party = row['speakerparty']
                partytag = party + '_' + congress
                congresstag = 'CONGRESS_' + congress
                tokens = text.split()
                if self.bigram and self.trigram:
                    self.words = self.trigram[self.bigram[tokens]]
                elif self.bigram and not self.trigram:
                    self.words = self.bigram[tokens]
                else:
                    self.words = tokens
                self.tags = [partytag, congresstag]
                yield self.speeches(self.words, self.tags)
                    
class PhraseIterator:
    def __init__(self, folder_path):
        self.folder_path = folder_path

    def __iter__(self):
        # Increase the field size limit- I was running into issues with csv exceeding the default limit in csv packaga
        csv.field_size_limit(sys.maxsize)
        
        # instead of just taking in one file with all the text, this will iterate through every folder in my folder path
        for root, dirs, files in os.walk(self.folder_path):
            for file in files:
                if file.endswith('.csv'):
                    file_path = os.path.join(root, file)
                    print(f"Processing {file_path}")
                    with open(file_path, 'r', newline='', encoding='utf-8') as f:
                        reader = csv.DictReader(f, delimiter=',')
                        for row in reader:
                            text = row['speechtext_preprocessed']
                            yield text.split()

In [4]:
if __name__=='__main__':
    folder_path = 'corpus_data/lipad'
    savepath = 'model/final_model'

    iterator = PhraseIterator(folder_path)

    phrases = Phrases(iterator)
    bigram = Phraser(phrases)
    tphrases = Phrases(bigram[iterator])
    trigram = Phraser(tphrases)

    model0 = Doc2Vec(vector_size=200, window=20, min_count=50, workers=8, epochs=5)
    model0.build_vocab(CorpusIterator(folder_path, bigram=bigram, trigram=trigram))
    model0.train(CorpusIterator(folder_path, bigram=bigram, trigram=trigram), total_examples=model0.corpus_count, epochs=model0.epochs)
    model0.save(savepath)

Processing corpus_data/lipad/2013/11/2013-11-8.csv
Processing corpus_data/lipad/2013/11/2013-11-22.csv
Processing corpus_data/lipad/2013/11/2013-11-20.csv
Processing corpus_data/lipad/2013/11/2013-11-21.csv
Processing corpus_data/lipad/2013/11/2013-11-19.csv
Processing corpus_data/lipad/2013/11/2013-11-25.csv
Processing corpus_data/lipad/2013/11/2013-11-18.csv
Processing corpus_data/lipad/2013/11/2013-11-26.csv
Processing corpus_data/lipad/2013/11/2013-11-27.csv
Processing corpus_data/lipad/2013/11/2013-11-29.csv
Processing corpus_data/lipad/2013/11/2013-11-28.csv
Processing corpus_data/lipad/2013/11/2013-11-6.csv
Processing corpus_data/lipad/2013/11/2013-11-7.csv
Processing corpus_data/lipad/2013/11/2013-11-5.csv
Processing corpus_data/lipad/2013/11/2013-11-4.csv
Processing corpus_data/lipad/2013/6/2013-6-18.csv
Processing corpus_data/lipad/2013/6/2013-6-19.csv
Processing corpus_data/lipad/2013/6/2013-6-6.csv
Processing corpus_data/lipad/2013/6/2013-6-7.csv
Processing corpus_data/lipa

Processing corpus_data/lipad/2014/10/2014-10-21.csv
Processing corpus_data/lipad/2014/10/2014-10-23.csv
Processing corpus_data/lipad/2014/10/2014-10-3.csv
Processing corpus_data/lipad/2014/10/2014-10-2.csv
Processing corpus_data/lipad/2014/10/2014-10-1.csv
Processing corpus_data/lipad/2014/10/2014-10-6.csv
Processing corpus_data/lipad/2014/10/2014-10-7.csv
Processing corpus_data/lipad/2014/4/2014-4-7.csv
Processing corpus_data/lipad/2014/4/2014-4-4.csv
Processing corpus_data/lipad/2014/4/2014-4-1.csv
Processing corpus_data/lipad/2014/4/2014-4-3.csv
Processing corpus_data/lipad/2014/4/2014-4-2.csv
Processing corpus_data/lipad/2014/4/2014-4-30.csv
Processing corpus_data/lipad/2014/4/2014-4-28.csv
Processing corpus_data/lipad/2014/4/2014-4-29.csv
Processing corpus_data/lipad/2014/4/2014-4-11.csv
Processing corpus_data/lipad/2014/4/2014-4-10.csv
Processing corpus_data/lipad/2014/4/2014-4-9.csv
Processing corpus_data/lipad/2014/4/2014-4-8.csv
Processing corpus_data/lipad/2014/3/2014-3-3.csv

Processing corpus_data/lipad/2012/11/2012-11-30.csv
Processing corpus_data/lipad/2012/11/2012-11-8.csv
Processing corpus_data/lipad/2012/11/2012-11-26.csv
Processing corpus_data/lipad/2012/11/2012-11-27.csv
Processing corpus_data/lipad/2012/11/2012-11-6.csv
Processing corpus_data/lipad/2012/11/2012-11-7.csv
Processing corpus_data/lipad/2012/11/2012-11-5.csv
Processing corpus_data/lipad/2012/11/2012-11-29.csv
Processing corpus_data/lipad/2012/11/2012-11-28.csv
Processing corpus_data/lipad/2012/11/2012-11-1.csv
Processing corpus_data/lipad/2012/11/2012-11-2.csv
Processing corpus_data/lipad/2012/6/2012-6-21.csv
Processing corpus_data/lipad/2012/6/2012-6-20.csv
Processing corpus_data/lipad/2012/6/2012-6-18.csv
Processing corpus_data/lipad/2012/6/2012-6-19.csv
Processing corpus_data/lipad/2012/6/2012-6-8.csv
Processing corpus_data/lipad/2012/6/2012-6-1.csv
Processing corpus_data/lipad/2012/6/2012-6-5.csv
Processing corpus_data/lipad/2012/6/2012-6-4.csv
Processing corpus_data/lipad/2012/6/20

Processing corpus_data/lipad/1944/3/1944-3-16.csv
Processing corpus_data/lipad/1944/3/1944-3-17.csv
Processing corpus_data/lipad/1944/3/1944-3-29.csv
Processing corpus_data/lipad/1944/3/1944-3-28.csv
Processing corpus_data/lipad/1944/3/1944-3-14.csv
Processing corpus_data/lipad/1944/3/1944-3-10.csv
Processing corpus_data/lipad/1944/3/1944-3-13.csv
Processing corpus_data/lipad/1944/3/1944-3-23.csv
Processing corpus_data/lipad/1944/3/1944-3-20.csv
Processing corpus_data/lipad/1944/3/1944-3-21.csv
Processing corpus_data/lipad/1944/3/1944-3-31.csv
Processing corpus_data/lipad/1944/3/1944-3-24.csv
Processing corpus_data/lipad/1944/3/1944-3-30.csv
Processing corpus_data/lipad/1944/3/1944-3-27.csv
Processing corpus_data/lipad/1944/3/1944-3-2.csv
Processing corpus_data/lipad/1944/3/1944-3-3.csv
Processing corpus_data/lipad/1944/3/1944-3-7.csv
Processing corpus_data/lipad/1944/3/1944-3-6.csv
Processing corpus_data/lipad/1944/2/1944-2-21.csv
Processing corpus_data/lipad/1944/2/1944-2-22.csv
Proc

Processing corpus_data/lipad/1943/5/1943-5-17.csv
Processing corpus_data/lipad/1943/5/1943-5-27.csv
Processing corpus_data/lipad/1943/5/1943-5-26.csv
Processing corpus_data/lipad/1943/5/1943-5-18.csv
Processing corpus_data/lipad/1943/5/1943-5-24.csv
Processing corpus_data/lipad/1943/5/1943-5-31.csv
Processing corpus_data/lipad/1943/5/1943-5-25.csv
Processing corpus_data/lipad/1943/5/1943-5-19.csv
Processing corpus_data/lipad/1943/5/1943-5-21.csv
Processing corpus_data/lipad/1943/5/1943-5-20.csv
Processing corpus_data/lipad/1988/9/1988-9-13.csv
Processing corpus_data/lipad/1988/9/1988-9-28.csv
Processing corpus_data/lipad/1988/9/1988-9-14.csv
Processing corpus_data/lipad/1988/9/1988-9-15.csv
Processing corpus_data/lipad/1988/9/1988-9-29.csv
Processing corpus_data/lipad/1988/9/1988-9-16.csv
Processing corpus_data/lipad/1988/9/1988-9-1.csv
Processing corpus_data/lipad/1988/9/1988-9-27.csv
Processing corpus_data/lipad/1988/9/1988-9-26.csv
Processing corpus_data/lipad/1988/9/1988-9-30.csv
P

...

Processing corpus_data/lipad/1909/1/1909-1-26.csv
Processing corpus_data/lipad/1909/1/1909-1-27.csv
Processing corpus_data/lipad/1909/1/1909-1-22.csv
Processing corpus_data/lipad/1909/1/1909-1-20.csv
Processing corpus_data/lipad/1909/1/1909-1-29.csv
Processing corpus_data/lipad/1909/1/1909-1-28.csv
Processing corpus_data/lipad/1909/4/1909-4-15.csv
Processing corpus_data/lipad/1909/4/1909-4-29.csv
Processing corpus_data/lipad/1909/4/1909-4-28.csv
Processing corpus_data/lipad/1909/4/1909-4-14.csv
Processing corpus_data/lipad/1909/4/1909-4-16.csv
Processing corpus_data/lipad/1909/4/1909-4-13.csv
Processing corpus_data/lipad/1909/4/1909-4-6.csv
Processing corpus_data/lipad/1909/4/1909-4-20.csv
Processing corpus_data/lipad/1909/4/1909-4-21.csv
Processing corpus_data/lipad/1909/4/1909-4-7.csv
Processing corpus_data/lipad/1909/4/1909-4-5.csv
Processing corpus_data/lipad/1909/4/1909-4-23.csv
Processing corpus_data/lipad/1909/4/1909-4-22.csv
Processing corpus_data/lipad/1909/4/1909-4-26.csv
Pro

Processing corpus_data/lipad/1931/5/1931-5-7.csv
Processing corpus_data/lipad/1931/5/1931-5-5.csv
Processing corpus_data/lipad/1931/5/1931-5-26.csv
Processing corpus_data/lipad/1931/5/1931-5-27.csv
Processing corpus_data/lipad/1931/5/1931-5-22.csv
Processing corpus_data/lipad/1931/5/1931-5-1.csv
Processing corpus_data/lipad/1931/5/1931-5-20.csv
Processing corpus_data/lipad/1931/5/1931-5-21.csv
Processing corpus_data/lipad/1931/5/1931-5-11.csv
Processing corpus_data/lipad/1931/5/1931-5-13.csv
Processing corpus_data/lipad/1931/5/1931-5-12.csv
Processing corpus_data/lipad/1931/5/1931-5-8.csv
Processing corpus_data/lipad/1931/5/1931-5-29.csv
Processing corpus_data/lipad/1931/5/1931-5-15.csv
Processing corpus_data/lipad/1931/5/1931-5-14.csv
Processing corpus_data/lipad/1931/5/1931-5-28.csv
Processing corpus_data/lipad/1907/8/1907-8-1.csv
Processing corpus_data/lipad/1938/7/1938-7-1.csv
Processing corpus_data/lipad/1938/6/1938-6-7.csv
Processing corpus_data/lipad/1938/6/1938-6-6.csv
Processi

Processing corpus_data/lipad/2005/10/2005-10-3.csv
Processing corpus_data/lipad/2005/10/2005-10-17.csv
Processing corpus_data/lipad/2005/10/2005-10-5.csv
Processing corpus_data/lipad/2005/10/2005-10-4.csv
Processing corpus_data/lipad/2005/10/2005-10-6.csv
Processing corpus_data/lipad/2005/10/2005-10-7.csv
Processing corpus_data/lipad/2005/4/2005-4-21.csv
Processing corpus_data/lipad/2005/4/2005-4-20.csv
Processing corpus_data/lipad/2005/4/2005-4-22.csv
Processing corpus_data/lipad/2005/4/2005-4-5.csv
Processing corpus_data/lipad/2005/4/2005-4-4.csv
Processing corpus_data/lipad/2005/4/2005-4-6.csv
Processing corpus_data/lipad/2005/4/2005-4-18.csv
Processing corpus_data/lipad/2005/4/2005-4-19.csv
Processing corpus_data/lipad/2005/4/2005-4-7.csv
Processing corpus_data/lipad/2005/4/2005-4-14.csv
Processing corpus_data/lipad/2005/4/2005-4-15.csv
Processing corpus_data/lipad/2005/4/2005-4-12.csv
Processing corpus_data/lipad/2005/4/2005-4-13.csv
Processing corpus_data/lipad/2005/4/2005-4-11.c

Processing corpus_data/lipad/2002/2/2002-2-8.csv
Processing corpus_data/lipad/2002/2/2002-2-7.csv
Processing corpus_data/lipad/2002/2/2002-2-6.csv
Processing corpus_data/lipad/2002/2/2002-2-4.csv
Processing corpus_data/lipad/2002/2/2002-2-5.csv
Processing corpus_data/lipad/2002/2/2002-2-1.csv
Processing corpus_data/lipad/2002/2/2002-2-28.csv
Processing corpus_data/lipad/2002/5/2002-5-10.csv
Processing corpus_data/lipad/2002/5/2002-5-8.csv
Processing corpus_data/lipad/2002/5/2002-5-9.csv
Processing corpus_data/lipad/2002/5/2002-5-29.csv
Processing corpus_data/lipad/2002/5/2002-5-28.csv
Processing corpus_data/lipad/2002/5/2002-5-31.csv
Processing corpus_data/lipad/2002/5/2002-5-2.csv
Processing corpus_data/lipad/2002/5/2002-5-3.csv
Processing corpus_data/lipad/2002/5/2002-5-24.csv
Processing corpus_data/lipad/2002/5/2002-5-30.csv
Processing corpus_data/lipad/2002/5/2002-5-1.csv
Processing corpus_data/lipad/2002/5/2002-5-27.csv
Processing corpus_data/lipad/2002/5/2002-5-23.csv
Processing 

Processing corpus_data/lipad/2004/10/2004-10-13.csv
Processing corpus_data/lipad/2004/10/2004-10-12.csv
Processing corpus_data/lipad/2004/4/2004-4-21.csv
Processing corpus_data/lipad/2004/4/2004-4-20.csv
Processing corpus_data/lipad/2004/4/2004-4-22.csv
Processing corpus_data/lipad/2004/4/2004-4-23.csv
Processing corpus_data/lipad/2004/4/2004-4-27.csv
Processing corpus_data/lipad/2004/4/2004-4-26.csv
Processing corpus_data/lipad/2004/4/2004-4-1.csv
Processing corpus_data/lipad/2004/4/2004-4-30.csv
Processing corpus_data/lipad/2004/4/2004-4-19.csv
Processing corpus_data/lipad/2004/4/2004-4-2.csv
Processing corpus_data/lipad/2004/4/2004-4-28.csv
Processing corpus_data/lipad/2004/4/2004-4-29.csv
Processing corpus_data/lipad/2004/3/2004-3-29.csv
Processing corpus_data/lipad/2004/3/2004-3-12.csv
Processing corpus_data/lipad/2004/3/2004-3-11.csv
Processing corpus_data/lipad/2004/3/2004-3-10.csv
Processing corpus_data/lipad/2004/3/2004-3-9.csv
Processing corpus_data/lipad/2004/3/2004-3-8.csv


## Checking to make sure that worked

In [11]:
# Load the saved model
loaded_model = Doc2Vec.load('model/updated_model')

# Now you can use the loaded model to infer vectors for new documents or to find similar documents
# For example, you can infer a vector for a new document
new_document = "New legislation will help children"
inferred_vector = loaded_model.infer_vector(new_document.split())

# Or you can find similar documents
similar_documents = loaded_model.docvecs.most_similar([inferred_vector])

# Print the most similar documents
print("Similar documents:")
for doc_id, similarity in similar_documents:
    print(f"Document ID: {doc_id}, Similarity: {similarity}")
    
#Doc2Vec.save(loaded_model)
    
# YAYAYAYAYA

Similar documents:
Document ID: CONGRESS_1907, Similarity: 0.48954659700393677
Document ID: _1907, Similarity: 0.4892134964466095
Document ID: Independent Liberal_1927, Similarity: 0.4726344347000122
Document ID: New Democracy_1945, Similarity: 0.4088713228702545
Document ID: CONGRESS_1961, Similarity: 0.3813115656375885
Document ID: CONGRESS_1959, Similarity: 0.3757036626338959
Document ID: CONGRESS_1974, Similarity: 0.37384849786758423
Document ID: CONGRESS_1960, Similarity: 0.36545488238334656
Document ID: CONGRESS_1972, Similarity: 0.35769641399383545
Document ID: CONGRESS_1956, Similarity: 0.3563438057899475


/var/folders/r_/rw1ty4x55gl73b77mkvn_bkc0000gn/T/ipykernel_16189/3988676889.py:10: DeprecationWarning: Call to deprecated `docvecs` (The `docvecs` property has been renamed `dv`.).
  similar_documents = loaded_model.docvecs.most_similar([inferred_vector])
